In [1]:
import pandas as pd
import geopandas as gpd
import bokeh
import numpy as np
import matplotlib
import fiona

import datetime
from datetime import timedelta

# visualization
import matplotlib.pyplot as plt
import folium
# from folium.features import GeoJson, GeoJsonTooltip, GeoJsonPopup
import plotly.express as px
from shapely.geometry import Point

from pyproj import CRS

# Base Case Scenario

In [2]:
shp = './Base/Shapefiles/'
geojson = './Base/Shapefiles/GeoJSON/'
# read the stop shapefile
gdStopID = gpd.read_file(geojson+"unique_StopIDs.geojson")
gdStopID["X"]=gdStopID['geometry'].y
gdStopID["Y"]=gdStopID['geometry'].x
gdStopID.to_csv(shp+"stops.csv")
gdStops = pd.read_csv(shp+"stops.csv")
gdStopID.drop(['geometry'], axis=1, inplace=True)
# creating a geometry column 
geometry = [Point(xy) for xy in zip(gdStopID['X'], gdStopID['Y'])]
# Coordinate reference system : 3520 --> WGS84
crs = {'init': 'epsg:3520'}
# Creating a Geographic data frame 
gdStopID = gpd.GeoDataFrame(gdStopID, crs=crs, geometry=geometry)

# gdStopID = gdStopID.set_crs(epsg=3520)
gdStopID['geometry']= gdStopID['geometry'].to_crs(epsg=4326)
gdStopID = gdStopID.to_crs(epsg=4326)

gdStopID = gpd.GeoDataFrame(gdStopID,geometry=gdStopID['geometry'])

# read the census tract shapefile
gCT = gpd.read_file("./SHPs/BG_Atlanta_GEOID10.shp")
gCT = gCT.set_crs(epsg=4326)
gCT['geometry']= gCT['geometry'].to_crs(epsg=4326)
gCT = gCT.to_crs(epsg=4326)
gCT.to_file(geojson+'BG_Atlanta_GEOID10.geojson', driver='GeoJSON')
gCT = gpd.read_file(geojson+'BG_Atlanta_GEOID10.geojson', driver='GeoJSON')

# Final step of coverting the polygon file to centroid (point file). 
# Use this feature class for plotting
gCT["UID"] = gCT["GEOID10"]
stops_within_CT = gpd.sjoin(gdStopID,gCT, how="inner", op='within')

c:\users\goyal\.virtualenvs\to_upload-c-7jcarz\lib\site-packages\pyproj\crs\crs.py:68: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
c:\users\goyal\.virtualenvs\to_upload-c-7jcarz\lib\site-packages\IPython\core\interactiveshell.py:3364: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):


In [3]:
shp = './Base/Shapefiles/'
geojson = './Base/Shapefiles/GeoJSON/'
# read the stop shapefile
gdStopID = gpd.read_file(geojson+"unique_StopIDs.geojson")

gdStopID["X"]=gdStopID['geometry'].y
gdStopID["Y"]=gdStopID['geometry'].x
gdStopID.drop(['geometry'], axis=1, inplace=True)
geometry = [Point(xy) for xy in zip(gdStopID["X"], gdStopID["Y"])]
# Coordinate reference system : WGS84
crs = {'init': 'epsg:3520'}
# Creating a Geographic data frame 
gdStopID = gpd.GeoDataFrame(gdStopID, crs=crs, geometry=geometry)

# gdStopID = gdStopID.set_crs(epsg=3520)
gdStopID['geometry']= gdStopID['geometry'].to_crs(epsg=4326)
gdStopID = gdStopID.to_crs(epsg=4326)

gdStopID = gpd.GeoDataFrame(gdStopID,geometry=gdStopID['geometry'])
gdStopID = gdStopID.rename(columns={"ID" : "stopID", "Boardings":"total_riders"})
gdStopID["total_riders"]=gdStopID["total_riders"]*5
gdStopID["No_of_bus_stops"]=1

# read the block group shapefile
gBG = gpd.read_file("./SHPs/BG_Atlanta_GEOID10.shp")
gBG = gBG.set_crs(epsg=4326)
gBG['geometry']= gBG['geometry'].to_crs(epsg=4326)
gBG = gBG.to_crs(epsg=4326)
gBG.to_file(geojson+'BG_Atlanta_GEOID10.geojson', driver='GeoJSON')
gBG = gpd.read_file(geojson+'BG_Atlanta_GEOID10.geojson', driver='GeoJSON')

# Final step of coverting the polygon file to centroid (point file). 
gBG["GEOID10_2"]=(pd.to_numeric(gBG["GEOID10_2"])).replace(np.nan,0)
gBG["GEOID10"]=(pd.to_numeric(gBG["GEOID10"])).replace(np.nan,0)
# Use this feature class for plotting
gBG["UID"] = gBG["GEOID10_2"] + gBG["GEOID10"]
stops_within_BG = gpd.sjoin(gdStopID,gBG, how="inner", op='within')

stops_within_BG_rail =stops_within_BG[stops_within_BG["mode"]=="rail"].copy()
stops_within_BG =stops_within_BG[stops_within_BG["mode"]=="bus"].copy()
stops = stops_within_BG.groupby("UID").agg({
                                                "stopID":(','.join),
                                                "total_riders":"sum",
                                                "mode":"first",
                                                "No_of_bus_stops":"sum"
                                            }).reset_index()

BG_with_stops = pd.merge(gBG, stops, how="left",left_on="UID", right_on="UID")
col_list = ["UID","stopID","total_riders", "mode","No_of_bus_stops","geometry"]
BG_with_stops = BG_with_stops[col_list]
col_list = ["stopID","total_riders", "No_of_bus_stops"]
BG_with_stops[col_list] = BG_with_stops[col_list].replace(np.nan,0)

# BG_with_stops

import copy
centroid_BG_with_stops = BG_with_stops.copy()

centroid_BG_with_stops['geometry']= centroid_BG_with_stops['geometry'].to_crs(epsg=4326)

centroid_BG_with_stops = centroid_BG_with_stops.to_crs(epsg=4326)
centroid_BG_with_stops["centroid"] = centroid_BG_with_stops.centroid
centroid_BG_with_stops = centroid_BG_with_stops.set_geometry("centroid").to_crs(epsg=4326)


### For Rail

stops_rail = stops_within_BG_rail.groupby("UID").agg({
                                                "stopID":(','.join),
                                                "total_riders":"sum",
                                                "mode":"first",
                                                "No_of_bus_stops":"sum"
                                            }).reset_index()

BG_with_stops_rail = pd.merge(gBG, stops_rail, how="left",left_on="UID", right_on="UID")
col_list = ["UID","stopID","total_riders", "mode","No_of_bus_stops","geometry"]
BG_with_stops_rail = BG_with_stops_rail[col_list]
col_list = ["stopID","total_riders", "No_of_bus_stops"]
BG_with_stops_rail[col_list] = BG_with_stops_rail[col_list].replace(np.nan,0)

# BG_with_stops_rail

import copy
centroid_BG_with_stops_rail = BG_with_stops_rail.copy()

centroid_BG_with_stops_rail['geometry']= centroid_BG_with_stops_rail['geometry'].to_crs(epsg=4326)

centroid_BG_with_stops_rail = centroid_BG_with_stops_rail.to_crs(epsg=4326)
centroid_BG_with_stops_rail["centroid"] = centroid_BG_with_stops_rail.centroid
centroid_BG_with_stops_rail = centroid_BG_with_stops_rail.set_geometry("centroid").to_crs(epsg=4326)

c:\users\goyal\.virtualenvs\to_upload-c-7jcarz\lib\site-packages\pyproj\crs\crs.py:68: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
c:\users\goyal\.virtualenvs\to_upload-c-7jcarz\lib\site-packages\IPython\core\interactiveshell.py:3364: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):
C:\Users\Goyal\AppData\Local\Temp/ipykernel_18796/97070498.py:62: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid_BG_with_stops["centroid"] = centroid_BG_with

## Map - Base Case

In [4]:
# Add the Census Tract on the Map. Make the boundaries black, while the polygon hollow. 
import folium
from folium.features import GeoJsonPopup, GeoJsonTooltip
import branca
import branca.colormap as cm
import json
from branca.element import Template, MacroElement

template = """
{% macro html(this, kwargs) %}

<!doctype html>
<html lang="en">
<head>
  <meta charset="utf-8">
  <meta name="viewport" content="width=device-width, initial-scale=1">
  <title>jQuery UI Draggable - Default functionality</title>
  <link rel="stylesheet" href="//code.jquery.com/ui/1.12.1/themes/base/jquery-ui.css">

  <script src="https://code.jquery.com/jquery-1.12.4.js"></script>
  <script src="https://code.jquery.com/ui/1.12.1/jquery-ui.js"></script>
  
  <script>
  $( function() {
    $( "#maplegend" ).draggable({
                    start: function (event, ui) {
                        $(this).css({
                            right: "auto",
                            top: "auto",
                            bottom: "auto"
                        });
                    }
                });
});

  </script>
</head>
<body>
 
<div id='maplegend' class='maplegend' 
    style='position: absolute; z-index:9999; border:2px solid grey; background-color:rgba(255, 255, 255, 0.8);
     border-radius:6px; padding: 10px; font-size:14px; right: 20px; bottom: 20px;'>     
    <div class='legend-title'>Map Legend</div>
    <div class='legend-scale'>
      <ul class='legend-labels'>
        <li><Circle_500 style='background:#DC267F;opacity:0.7;'></Circle_500>  500 Riders</li>
        <br>
        <li><Circle_100 style='background:#DC267F;opacity:0.7;'></Circle_100>  100 Riders</li>
        <br>
        <li><Circle_10 style='background:#DC267F;opacity:0.7;'></Circle_10>    10 Riders</li>
      </ul>
    </div>
</div>
 
</body>
</html>

<style type='text/css'>
  .maplegend .legend-title {
    text-align: left;
    margin-bottom: 5px;
    font-weight: bold;
    font-size: 90%;
    }
  .maplegend .legend-scale ul {
    margin: 0;
    margin-bottom: 5px;
    padding: 0;
    float: left;
    list-style: none;
    }
  .maplegend .legend-scale ul li {
    font-size: 80%;
    overflow: none;
    list-style: none;
    list-style-position: inside;
    margin-left: 0;
    line-height: 18px;
    margin-bottom: 2px;
    text-align:center;
    justify-content: center;
    display: inline-block;
    }
  .maplegend ul.legend-labels li span {
    display: inline-block;
    overflow: none;
    float: left;
    height: 16px;
    text-align: center;
    width: 30px;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    }
  .maplegend ul.legend-labels li Circle_10 {
    float: left;
    height: 5px;
    width: 5px;
    display: inline-block;
    overflow: none;
    background-color: #004;
    border-radius: 50%;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    text-align:center;
    justify-content: center;
    clear="left",
    }
  .maplegend ul.legend-labels li Circle_100 {
    float: left;
    height: 15px;
    width: 15px;
    display: inline-block;
    overflow: none;
    background-color: #004;
    border-radius: 50%;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    text-align:center;
    justify-content: center;
    clear="left",
    }
  .maplegend ul.legend-labels li Circle_500 {
    float: left;
    height: 30px;
    width: 30px;
    display: inline-block;
    overflow: none;
    background-color: #004;
    border-radius: 50%;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    text-align:center;
    justify-content: center;
    clear="left",
    }
  .maplegend .legend-source {
    font-size: 80%;
    color: #777;
    clear: both;
    }
  .maplegend a {
    color: #777;
    }
</style>
{% endmacro %}"""


colormap = branca.colormap.LinearColormap(
    vmin=BG_with_stops["total_riders"].min(),
    vmax=BG_with_stops["total_riders"].max(),
    colors=["red", "orange", "lightblue", "green", "darkgreen"],
    caption="Total riders in base scenario",
)

def get_color_opacity(no_of_busstops):
    if no_of_busstops > 1:
        return 0.6
    else:
        return 0.4
        


latlong=[33.7489954,-84.3879824]
m = folium.Map(location=latlong,tiles="Stamen Toner",zoom_start=11,control_scale=True)


###### Create Centroid Markers

import pandas as pd
import folium
from folium.plugins import FastMarkerCluster, MarkerCluster
from folium import FeatureGroup, LayerControl, Map

def get_circle_radius(passengers):
#     r = abs(passengers)/10
    r = abs(passengers)
    radius=0
    if r<=0:
        radius=0
    else:
        radius=r/25

    return radius

# populate rail points
# feature_group = folium.FeatureGroup(name="Rail")
# # centroid_BG_with_stops_rail= centroid_BG_with_stops_rail["mode"].dropna()
# for index, row in centroid_BG_with_stops_rail[centroid_BG_with_stops_rail['mode'].notna()].iterrows():
#     popup_text = "<br> <b>Total Rail Stops:</b> {:,}<br> <b>Total Ridership:</b> {:,}".format(                      
#                       row["No_of_bus_stops"],
#                       row["total_riders"]
#                       )
#     tooltip_text = "<br> <b>Total Rail Stops:</b> {:,}<br> <b>Total Ridership:</b> {:,}".format(                      
#                       row["No_of_bus_stops"],
#                       row["total_riders"]
#                       ) 
#     folium.Circle(location=[row["centroid"].y,row["centroid"].x],
#                         radius= get_circle_radius(row["total_riders"]),
#                         color="#00325a",
#                         popup=(popup_text),
#                         tooltip = (tooltip_text),
#                         fill=True, fill_opacity=0.7).add_to(feature_group)
# feature_group.add_to(m)
# populate bus points
feature_group = folium.FeatureGroup(name="Bus")
for index, row in centroid_BG_with_stops[centroid_BG_with_stops['mode'].notna()].iterrows():
    popup_text = "<br> <b>Total Bus Stops:</b> {:,}<br> <b>Total Ridership:</b> {:,}".format(                      
                      row["No_of_bus_stops"],
                      row["total_riders"]
                      )
    tooltip_text = "<br> <b>Total Bus Stops:</b> {:,}<br> <b>Total Ridership:</b> {:,}".format(                      
                      row["No_of_bus_stops"],
                      row["total_riders"]
                      ) 
    folium.Circle(location=[row["centroid"].y,row["centroid"].x],
                        radius= get_circle_radius(row["total_riders"]),
                        color="#564d3c",
                        popup=(popup_text),
                        tooltip = (tooltip_text),
                        fill=True, fill_opacity=0.7).add_to(feature_group)
feature_group.add_to(m)


folium.LayerControl().add_to(m)

macro = MacroElement()
macro._template = Template(template)

m.get_root().add_child(macro)

map_title = "Atlanta - Base Case Scenario"
title_html = '''
             <h3 align="center" style="font-size:16px"><b>{}</b></h3>
             '''.format(map_title)
m.get_root().html.add_child(folium.Element(title_html))
m.save('Base_Scenario_Atlanta_BG.html')
m

# HiPT Ridership Scenario

In [5]:
shp = './HiPT/Shapefiles/'
geojson = './HiPT/Shapefiles/GeoJSON/'
# read the stop shapefile
gdStopIDLI = gpd.read_file(geojson+"unique_StopIDs.geojson")
gdStopIDLI["X"]=gdStopIDLI['geometry'].y
gdStopIDLI["Y"]=gdStopIDLI['geometry'].x
gdStopIDLI.to_csv(shp+"stops.csv")
gdStops = pd.read_csv(shp+"stops.csv")
gdStopIDLI.drop(['geometry'], axis=1, inplace=True)
# creating a geometry column 
geometry = [Point(xy) for xy in zip(gdStopIDLI['X'], gdStopIDLI['Y'])]
# Coordinate reference system : 3520 --> WGS84
crs = {'init': 'epsg:3520'}
# Creating a Geographic data frame 
gdStopIDLI = gpd.GeoDataFrame(gdStopIDLI, crs=crs, geometry=geometry)

# gdStopIDLI = gdStopIDLI.set_crs(epsg=3520)
gdStopIDLI['geometry']= gdStopIDLI['geometry'].to_crs(epsg=4326)
gdStopIDLI = gdStopIDLI.to_crs(epsg=4326)

gdStopIDLI = gpd.GeoDataFrame(gdStopIDLI,geometry=gdStopIDLI['geometry'])

# read the census tract shapefile
gCTLI = gpd.read_file("./SHPs/BG_Atlanta_GEOID10.shp")
gCTLI = gCTLI.set_crs(epsg=4326)
gCTLI['geometry']= gCTLI['geometry'].to_crs(epsg=4326)
gCTLI = gCTLI.to_crs(epsg=4326)
gCTLI.to_file(geojson+'BG_Atlanta_GEOID10.geojson', driver='GeoJSON')
gCTLI = gpd.read_file(geojson+'BG_Atlanta_GEOID10.geojson', driver='GeoJSON')

# Final step of coverting the polygon file to centroid (point file). 
# Use this feature class for plotting
gCTLI["UID"] = gCTLI["GEOID10"]
stops_within_BG_LI = gpd.sjoin(gdStopIDLI,gCTLI, how="inner", op='within')

shp = './HiPT/Shapefiles/'
geojson = './HiPT/Shapefiles/GeoJSON/'
# read the stop shapefile
gdStopIDLI = gpd.read_file(geojson+"unique_StopIDs.geojson")

gdStopIDLI["X"]=gdStopIDLI['geometry'].y
gdStopIDLI["Y"]=gdStopIDLI['geometry'].x
gdStopIDLI.drop(['geometry'], axis=1, inplace=True)
geometry = [Point(xy) for xy in zip(gdStopIDLI["X"], gdStopIDLI["Y"])]
# Coordinate reference system : WGS84
crs = {'init': 'epsg:3520'}
# Creating a Geographic data frame 
gdStopIDLI = gpd.GeoDataFrame(gdStopIDLI, crs=crs, geometry=geometry)

# gdStopIDLI = gdStopIDLI.set_crs(epsg=3520)
gdStopIDLI['geometry']= gdStopIDLI['geometry'].to_crs(epsg=4326)
gdStopIDLI = gdStopIDLI.to_crs(epsg=4326)

gdStopIDLI = gpd.GeoDataFrame(gdStopIDLI,geometry=gdStopIDLI['geometry'])
gdStopIDLI = gdStopIDLI.rename(columns={"ID" : "stopID", "Boardings":"total_riders"})
gdStopIDLI["total_riders"]=gdStopIDLI["total_riders"]*5
gdStopIDLI["No_of_bus_stops"]=1

# read the block group shapefile
gBGLI = gpd.read_file("./SHPs/BG_Atlanta_GEOID10.shp")
gBGLI = gBGLI.set_crs(epsg=4326)
gBGLI['geometry']= gBGLI['geometry'].to_crs(epsg=4326)
gBGLI = gBGLI.to_crs(epsg=4326)
gBGLI.to_file(geojson+'BG_Atlanta_GEOID10.geojson', driver='GeoJSON')
gBGLI = gpd.read_file(geojson+'BG_Atlanta_GEOID10.geojson', driver='GeoJSON')

# Final step of coverting the polygon file to centroid (point file). 
gBGLI["GEOID10_2"]=(pd.to_numeric(gBGLI["GEOID10_2"])).replace(np.nan,0)
gBGLI["GEOID10"]=(pd.to_numeric(gBGLI["GEOID10"])).replace(np.nan,0)
# Use this feature class for plotting
gBGLI["UID"] = gBGLI["GEOID10_2"] + gBGLI["GEOID10"]
stops_within_BG_LI = gpd.sjoin(gdStopIDLI,gBGLI, how="inner", op='within')

stops_within_BG_rail_LI =stops_within_BG_LI[stops_within_BG_LI["mode"]=="rail"].copy()
stops_within_BG_LI =stops_within_BG_LI[stops_within_BG_LI["mode"]=="bus"].copy()
stops_LI = stops_within_BG_LI.groupby("UID").agg({
                                                "stopID":(','.join),
                                                "total_riders":"sum",
                                                "mode":"first",
                                                "No_of_bus_stops":"sum"
                                            }).reset_index()

BG_with_stops_LI = pd.merge(gBGLI, stops_LI, how="left",left_on="UID", right_on="UID")
col_list = ["UID","stopID","total_riders", "mode","No_of_bus_stops","geometry"]
BG_with_stops_LI = BG_with_stops_LI[col_list]
col_list = ["stopID","total_riders", "No_of_bus_stops"]
BG_with_stops_LI[col_list] = BG_with_stops_LI[col_list].replace(np.nan,0)

# BG_with_stops_LI

import copy
centroid_BG_with_stops_LI = BG_with_stops_LI.copy()

centroid_BG_with_stops_LI['geometry']= centroid_BG_with_stops_LI['geometry'].to_crs(epsg=4326)

centroid_BG_with_stops_LI = centroid_BG_with_stops_LI.to_crs(epsg=4326)
centroid_BG_with_stops_LI["centroid"] = centroid_BG_with_stops_LI.centroid
centroid_BG_with_stops_LI = centroid_BG_with_stops_LI.set_geometry("centroid").to_crs(epsg=4326)


### For Rail

stops_rail_LI = stops_within_BG_rail_LI.groupby("UID").agg({
                                                "stopID":(','.join),
                                                "total_riders":"sum",
                                                "mode":"first",
                                                "No_of_bus_stops":"sum"
                                            }).reset_index()

BG_with_stops_LI_rail = pd.merge(gBGLI, stops_rail_LI, how="left",left_on="UID", right_on="UID")
col_list = ["UID","stopID","total_riders", "mode","No_of_bus_stops","geometry"]
BG_with_stops_LI_rail = BG_with_stops_LI_rail[col_list]
col_list = ["stopID","total_riders", "No_of_bus_stops"]
BG_with_stops_LI_rail[col_list] = BG_with_stops_LI_rail[col_list].replace(np.nan,0)

# BG_with_stops_LI_rail

import copy
centroid_BG_with_stops_LI_rail = BG_with_stops_LI_rail.copy()

centroid_BG_with_stops_LI_rail['geometry']= centroid_BG_with_stops_LI_rail['geometry'].to_crs(epsg=4326)

centroid_BG_with_stops_LI_rail = centroid_BG_with_stops_LI_rail.to_crs(epsg=4326)
centroid_BG_with_stops_LI_rail["centroid"] = centroid_BG_with_stops_LI_rail.centroid
centroid_BG_with_stops_LI_rail = centroid_BG_with_stops_LI_rail.set_geometry("centroid").to_crs(epsg=4326)



c:\users\goyal\.virtualenvs\to_upload-c-7jcarz\lib\site-packages\pyproj\crs\crs.py:68: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
c:\users\goyal\.virtualenvs\to_upload-c-7jcarz\lib\site-packages\IPython\core\interactiveshell.py:3364: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):
c:\users\goyal\.virtualenvs\to_upload-c-7jcarz\lib\site-packages\pyproj\crs\crs.py:68: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/sta

In [6]:
df2 = BG_with_stops.copy()
df3 = centroid_BG_with_stops_LI.copy()
df_merge = pd.merge(df2,df3, how="left",left_on="UID", right_on="UID")

df_merge.drop(['geometry_y', 'centroid'], axis=1, inplace=True)
df_merge['geometry']= df_merge['geometry_x'].to_crs(epsg=4326)
df_merge = df_merge.to_crs(epsg=4326)
df_merge["centroid"] = df_merge.centroid
df_merge = df_merge.set_geometry("centroid").to_crs(epsg=4326)

################################ RAIL ##############################################

df2_rail = BG_with_stops_rail.copy()
df3_rail = centroid_BG_with_stops_LI_rail.copy()
df_merge_rail = pd.merge(df2_rail,df3_rail, how="left",left_on="UID", right_on="UID")

df_merge_rail.drop(['geometry_y', 'centroid'], axis=1, inplace=True)
df_merge_rail['geometry']= df_merge_rail['geometry_x'].to_crs(epsg=4326)
df_merge_rail = df_merge_rail.to_crs(epsg=4326)
df_merge_rail["centroid"] = df_merge_rail.centroid
df_merge_rail = df_merge_rail.set_geometry("centroid").to_crs(epsg=4326)

############################# Percent difference ########################################
def percentage_change(col1,col2):
    return round(((col2 - col1) / col1)*100,0)
#########################################################################################

df_merge["total_riders_PCTDIFF"]= percentage_change(df_merge["total_riders_x"],df_merge["total_riders_y"])
df_merge_rail["total_riders_PCTDIFF"]= percentage_change(df_merge_rail["total_riders_x"],df_merge_rail["total_riders_y"])

C:\Users\Goyal\AppData\Local\Temp/ipykernel_18796/3367111784.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  df_merge["centroid"] = df_merge.centroid
C:\Users\Goyal\AppData\Local\Temp/ipykernel_18796/3367111784.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  df_merge_rail["centroid"] = df_merge_rail.centroid


## Map - HiPT Ridership Scenario

In [7]:
# Add the Census Tract on the Map. Make the boundaries black, while the polygon hollow. 
import folium
from folium.features import GeoJsonPopup, GeoJsonTooltip
import branca
import branca.colormap as cm
import json
from branca.element import Template, MacroElement

template = """
{% macro html(this, kwargs) %}

<!doctype html>
<html lang="en">
<head>
  <meta charset="utf-8">
  <meta name="viewport" content="width=device-width, initial-scale=1">
  <title>jQuery UI Draggable - Default functionality</title>
  <link rel="stylesheet" href="//code.jquery.com/ui/1.12.1/themes/base/jquery-ui.css">

  <script src="https://code.jquery.com/jquery-1.12.4.js"></script>
  <script src="https://code.jquery.com/ui/1.12.1/jquery-ui.js"></script>
  
  <script>
  $( function() {
    $( "#maplegend" ).draggable({
                    start: function (event, ui) {
                        $(this).css({
                            right: "auto",
                            top: "auto",
                            bottom: "auto"
                        });
                    }
                });
});
</script>

</head>
<body>
 
<div id='maplegend' class='maplegend' 
    style='position: absolute; z-index:9999; border:2px solid grey; background-color:rgba(255, 255, 255, 0.8);
     border-radius:6px; padding: 10px; font-size:36px; right: 20px; bottom: 20px;'>
     
<div class='legend-title'>Map Legend</div>
<div class='legend-scale'>
  <ul class='legend-labels'>
    <li><Circle_500 style='background:#564d3c;opacity:0.7;'></Circle_500>  500 Riders</li><br>
    <li><Circle_100 style='background:#564d3c;opacity:0.7;'></Circle_100>  100 Riders</li><br>
    <li><Circle_10 style='background:#564d3c;opacity:0.7;'></Circle_10>    10 Riders</li><br>
    <li><span style='background:#009e73;opacity:0.7;'></span>Color = Positive % riders</li><br>
    <li><span style='background:#EE442F;opacity:0.7;'></span>Color = Negative % riders</li>
  </ul>
</div>
</div>
 
</body>
</html>

<style type='text/css'>
  .maplegend .legend-title {
    text-align: left;
    margin-bottom: 5px;
    font-weight: bold;
    font-size: 90%;
    }
  .maplegend .legend-scale ul {
    margin: 0;
    margin-bottom: 5px;
    padding: 0;
    float: left;
    list-style: none;
    }
  .maplegend .legend-scale ul li {
    font-size: 80%;
    overflow: none;
    list-style: none;
    list-style-position: inside;
    margin-left: 0;
    line-height: 18px;
    margin-bottom: 2px;
    text-align:center;
    justify-content: center;
    display: inline-block;
    }
  .maplegend ul.legend-labels li span {
    display: inline-block;
    overflow: none;
    float: left;
    height: 16px;
    text-align: center;
    width: 30px;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    }
  .maplegend ul.legend-labels li Circle_10 {
    float: left;
    height: 5px;
    width: 5px;
    display: inline-block;
    overflow: none;
    background-color: #004;
    border-radius: 50%;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    text-align:center;
    justify-content: center;
    clear="left",
    }
  .maplegend ul.legend-labels li Circle_100 {
    float: left;
    height: 15px;
    width: 15px;
    display: inline-block;
    overflow: none;
    background-color: #004;
    border-radius: 50%;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    text-align:center;
    justify-content: center;
    clear="left",
    }
  .maplegend ul.legend-labels li Circle_500 {
    float: left;
    height: 30px;
    width: 30px;
    display: inline-block;
    overflow: none;
    background-color: #004;
    border-radius: 50%;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    text-align:center;
    justify-content: center;
    clear="left",
    }
  .maplegend .legend-source {
    font-size: 80%;
    color: #777;
    clear: both;
    }
  .maplegend a {
    color: #777;
    }
</style>
{% endmacro %}"""


class MoveColormap(MacroElement):
    """Moves the colormap to a given position.

    Parameters
    ----------
    colormap : branca.colormap.ColorMap
        The colormap to bind.
    """
    def __init__(self, layer, colormap):
        super(MoveColormap, self).__init__()
        self.layer = layer
        self.colormap = colormap
        self._template = Template(u"""
        {% macro script(this, kwargs) %}            
            {{this.colormap.get_name()}}.svg[0][0].style.background="white";            
            {{this.colormap.get_name()}}.svg[0][0].style.resize = "both";           
            {{this.colormap.get_name()}}.xAxis = d3.svg.axis()
            .scale({{this.get_name()}}.x)
            .orient("left")
            .tickSize(1)
            .tickValues({{ this.tick_labels }});
        {% endmacro %}
        """)
        
df_merge["total_riders_PCTDIFF"]=df_merge["total_riders_PCTDIFF"].replace([np.inf, -np.inf], 0)
#  {{this.colormap.get_name()}}.xAxis = this.svg.axis().orient("left"); 
# linear_color_green = cm.LinearColormap(["#198c19","#329932", "#007300", "#006600", "#005900", "#004c00","#004000","#003300","#002600"], 
#                            vmin=df_merge[df_merge["total_riders_PCTDIFF"]>=0]["total_riders_PCTDIFF"].min(), 
#                            vmax=df_merge[df_merge["total_riders_PCTDIFF"]>=0]["total_riders_PCTDIFF"].max(),
#                            caption = "Positive diff from the base and built scenario (in %)")

linear_color_green = cm.LinearColormap(["#63ACBE","#009e73"], 
                                     vmin=df_merge[df_merge["total_riders_PCTDIFF"]>=0]["total_riders_PCTDIFF"].min(), 
                                     vmax=df_merge[df_merge["total_riders_PCTDIFF"]>=0]["total_riders_PCTDIFF"].max()).to_step(10)

# # "#ff0000","#e50000","#cc0000","#b20000","#990000","#7f0000"
# linear_color_red = cm.LinearColormap(["#ff0000","#e50000","#cc0000","#b20000","#990000","#7f0000"], 
#                            vmin=abs(df_merge[df_merge["total_riders_PCTDIFF"]<-1]["total_riders_PCTDIFF"].min()), 
#                            vmax=abs(df_merge[df_merge["total_riders_PCTDIFF"]<-1]["total_riders_PCTDIFF"].max()),
#                            caption = "Negative diff from the base and built scenario (in %)")
# linear_color_red = cm.linear.Reds_07.to_step(10).scale(df_merge[df_merge["total_riders_PCTDIFF"]<-1]["total_riders_PCTDIFF"].max(),
#                                                       df_merge[df_merge["total_riders_PCTDIFF"]<-1]["total_riders_PCTDIFF"].min())

linear_color_red = cm.LinearColormap(["#EE442F","#F5793A"], 
                                     vmin=df_merge[df_merge["total_riders_PCTDIFF"]<-1]["total_riders_PCTDIFF"].min(), 
                                     vmax=df_merge[df_merge["total_riders_PCTDIFF"]<-1]["total_riders_PCTDIFF"].max(), caption ="% difference").to_step(10)

linear_color = cm.LinearColormap(colors=["#EE442F","#F5793A", "#d8d8d8","#cccccc", "#7fceb9","#009e73"],
                                 index=[df_merge["total_riders_PCTDIFF"].min(),-0.0001,+0.000,+0.1,100, df_merge["total_riders_PCTDIFF"].max()],
                                 vmin=df_merge["total_riders_PCTDIFF"].min(), 
                                 vmax=df_merge["total_riders_PCTDIFF"].max(),
                                 caption = "Difference from the base and built scenario (in %)"
                           )

def get_linear_color(total_riders_PCTDIFF):
    if total_riders_PCTDIFF>=0:
        return linear_color_green(total_riders_PCTDIFF)
    elif (total_riders_PCTDIFF<0 and total_riders_PCTDIFF>-1):
        return "#a6a6a6"
    else:
        return linear_color_red(total_riders_PCTDIFF)
    

def get_color(no_of_busstops):
    """Maps low values to red and high values to green."""
    if no_of_busstops > 0:
        return "#198c19"
    elif no_of_busstops < 0:
        return "#ff0000"
    else:
        return "#999999"

def get_color_opacity(no_of_busstops):
    """Maps low values to green and high values to red."""
    if no_of_busstops > 1:
        return 0.6
    else:
        return 0.4
    
latlong=[33.7489954,-84.3879824]
m = folium.Map(location=latlong,tiles='Stamen Toner',zoom_start=11,control_scale=True)

###### Create Centroid Markers

import pandas as pd
import folium
from folium.plugins import FastMarkerCluster, MarkerCluster
   
def get_circle_radius(built_riders):
    r = abs(built_riders)
    radius=0
    if r<=0:
        radius=0
    elif (r>0 and r<200):
        radius=75
    elif (r>200 and r<400):
        radius=100
    elif (r>400 and r<600):
        radius=125
    elif (r>600 and r<800):
        raidus=150
    elif (r>800 and r<1000):
        radius=175
    elif (r>1000 and r<1500):
        radius=200
    elif (r>1500 and r<2000):
        radius=225
    elif (r>2000 and r<2500):
        radius=250
    else:
        radius=300
    return radius

# populate rail points
# feature_group = folium.FeatureGroup(name="Rail")
# df_merge_rail["total_riders_PCTDIFF"]=df_merge_rail["total_riders_PCTDIFF"].replace([np.inf, -np.inf], 0)
# # centroid_BG_with_stops_rail= centroid_BG_with_stops_rail["mode"].dropna()
# for index, row in df_merge_rail[df_merge_rail["total_riders_PCTDIFF"].notna()].iterrows():
#     popup_text = "<br> <b>Total Bus Stops:</b> {:,}<br> <b>% Diff in Total Ridership:</b> {:,}%<br> <b>Total Ridership in build scenario:</b> {:,}<br>".format(                      
#                       row["No_of_bus_stops_x"],
#                       round(row["total_riders_PCTDIFF"],0),
#                       int(row["total_riders_y"]),
#                       )
#     tooltip_text = "<br> <b>Total Bus Stops:</b> {:,}<br> <b>% Diff in Total Ridership:</b> {:,}%<br> <b>Total Ridership in build scenario:</b> {:,}<br>".format(                      
#                       row["No_of_bus_stops_x"],
#                       round(row["total_riders_PCTDIFF"],0),
#                       int(row["total_riders_y"]),
#                       )
#     folium.Circle(location=[row["centroid"].y,row["centroid"].x],
#                         radius= get_circle_radius(row["total_riders_y"]),
#                         color="#00325a",
#                         popup=(popup_text),
#                         tooltip = (tooltip_text),
#                         fill=True, fill_opacity=0.9).add_to(feature_group)
# feature_group.add_to(m)
# # populate bus points
feature_group = folium.FeatureGroup(name="Bus")
df_merge["total_riders_PCTDIFF"]=df_merge["total_riders_PCTDIFF"].replace([np.inf, -np.inf], 0)
for index, row in df_merge[df_merge["total_riders_PCTDIFF"].notna()].iterrows():
    popup_text = "<br> <b>Total Bus Stops:</b> {:,}<br> <b>% Diff in Total Ridership:</b> {:,}%<br> <b>Total Ridership in build scenario:</b> {:,}<br>".format(                      
                      row["No_of_bus_stops_x"],
                      round(row["total_riders_PCTDIFF"],0),
                      int(row["total_riders_y"]),
                      )
    tooltip_text = "<br> <b>Total Bus Stops:</b> {:,}<br> <b>% Diff in Total Ridership:</b> {:,}%<br> <b>Total Ridership in build scenario:</b> {:,}<br>".format(                      
                      row["No_of_bus_stops_x"],
                      round(row["total_riders_PCTDIFF"],0),
                      int(row["total_riders_y"]),
                      )
# [f(x) if condition else g(x) for x in sequence] 
# 100 if t == 0 else 5;                   get_circle_radius(row["total_riders_y"])
#     print("PCT_Diff:{}".format(str(row["total_riders_PCTDIFF"])))
    folium.Circle(location=[row["centroid"].y,row["centroid"].x],
                        radius= get_circle_radius(row["total_riders_y"]),
                        color=linear_color(int(row["total_riders_PCTDIFF"])),
                        # color=get_linear_color(int(row["total_riders_PCTDIFF"])),
                        popup=(popup_text),
                        tooltip = (tooltip_text),
                        fill=True, 
                        fillcolor=get_linear_color(int(row["total_riders_PCTDIFF"])),
                        fill_opacity=0.9).add_to(feature_group)                                               
feature_group.add_to(m)


# m.add_child(linear_color_red).add_child(linear_color_green)
# m.add_child(MoveColormap(feature_group,linear_color_red)).add_child(MoveColormap(feature_group,linear_color_green))

# m.add_child(linear_color_red)
# m.add_child(linear_color_green)
m.add_child(folium.map.LayerControl('topright', collapsed= False))

macro = MacroElement()
macro._template = Template(template)

m.get_root().add_child(macro)

map_title = "High PT Ridership Routes Scenario"
title_html = '''
             <h3 align="center" style="font-size:16px"><b>{}</b></h3>
             '''.format(map_title) 
m.get_root().html.add_child(folium.Element(title_html))

m.save('PCT_Diff_Base_HiPTRidership_Scenario_Atlanta_BG_without_colorscale.html')
m

In [8]:
linear_color_red

In [9]:
linear_color_green

In [10]:
linear_color